# HPX + Cling + Jupyter
This tutorial works in a special Jupyter notebook that can be used in one of two ways:
* From this website: https://hpx-jupyter.cct.lsu.edu
* From the docker image: stevenrbrandt/fedora-hpx-cling
* Normally, each cell should contain declarations, e.g. definitions of functions,
  variables, or `#include` statements.
  <div style='border: solid black 1pt;'>
  ```#include <iostream>
using namespace std;```</div>
* If you wish to process an expression, e.g. ```cout << "hello world\n"``` you
  can put ```.expr``` at the front of the cell.
  <div style='border: solid black 1pt;'>
  ```.expr cout << "hello, world\n";```</div>
* Sometimes you will want to test a cell because you are uncertain whether
  it might cause a segfault or some other error that will kill your kernel.
  Othertimes, you might want to test a definition without permanently adding
  it to the current namespace. You can do this by prefixing your cell with
  ```.test```. Whatever is calculated in a test cell will be thrown away
  after evaluation and will not kill your kernel.
  <div style='border: solid black 1pt;'>
  ```.test.expr int foo[5];
foo[10] = 1;```</div>
## Docker Instructions
* Frist, install Docker on your local resource
* Second, start Docker, e.g. ```sudo service docker start```
* Third, run the fedora-hpx-cling container, e.g.

    <div style='border: solid black 1pt;'>```$ docker pull stevenrbrandt/fedora-hpx-cling
$ docker run -it -p 8000:8000 stevenrbrandt/fedora-hpx-cling```</div>
    
    After you do this, docker will respond with something like
    
    <div style='border: solid black 1pt;'>`http://0.0.0.0:8000/?token=5d1eb8a4797851910de481985a54c2fdc3be80280023bac5`</div>
    
    Paste that URL into your browser, and you will be able to interact with the notebook.
* Fourth, play with the existing ipynb files or create new ones.
* Fifth, save your work! This is an important step. If you simply quit the container, everything you did will be lost. To save your work, first find your docker image using ```docker ps```.

    <div style='border: solid black 1pt;'>```$ docker ps
CONTAINER ID        IMAGE                            COMMAND                  CREATED             STATUS              PORTS                    NAMES
4f806b5f4fb3        stevenrbrandt/fedora-hpx-cling   "/bin/sh -c 'jupyter "   11 minutes ago      Up 11 minutes       0.0.0.0:8000->8000/tcp   dreamy_turing```</div>

    Once you have it (in this case, it's 4f806b5f4fb3), you can use ```docker cp``` to transfer files to or from your image.
    
    <div style='border: solid black 1pt;'>```$ docker cp 4f806b5f4fb3:/home/jup/HPX_by_example.ipynb .
$ docker cp HPX_by_example.ipynb 4f806b5f4fb3:/home/jup```</div>

In [1]:
#include <hpx/hpx.hpp>

In [2]:
using namespace std;
using namespace hpx;

# What is a (the) Future?

Many ways to get hold of a future, simplest way is to use (std) async:

In [3]:
int universal_answer() { return 42; }
void deep_thought()
{
  future<int> promised_answer = async(util::annotated_function(&universal_answer,"universal answer"));
  // do other things for 7.5 million years
  cout << promised_answer.get() << endl; // prints 42
  apex::dump(true);
}

If we want to do something other than a declaration, use the ".expr" prefix.

In [4]:
.expr deep_thought()

42

Elapsed time: 65.7861 seconds
Cores detected: 4
Worker Threads observed: 2
Available CPU time: 131.572 seconds

Timer                                                :  #calls  |    mean  |   total  |  % total  
------------------------------------------------------------------------------------------------
                                           <unknown> :        1   0.00e+00   0.00e+00      0.000
                                           APEX MAIN :        1   6.58e+01   6.58e+01    100.000
                                     background_work :        1   2.01e-05   2.01e-05      0.000
                       call_startup_functions_action :        1   0.00e+00   0.00e+00      0.000
                              load_components_action :        1   0.00e+00   0.00e+00      0.000
                                            pre_main :        1   0.00e+00   0.00e+00      0.000
                                          run_helper :        1   0.00e+00   0.00e+00      0.000
         

# Compositional Facilities

In [5]:
future<string> make_string()
{
    future<int> f1 = async([]()->int { return 123; });
    future<string> f2 = f1.then(
      [](future<int> f) -> string
      {
        return to_string(f.get()); // here .get() won't block
      });
    return f2;
}

In [6]:
.expr cout << make_string().get() << endl << apex::dump(true);



Elapsed time: 5.3791 seconds
Cores detected: 4
Worker Threads observed: 2
Available CPU time: 10.7582 seconds

Timer                                                :  #calls  |    mean  |   total  |  % total  
------------------------------------------------------------------------------------------------
                                           <unknown> :        1   0.00e+00   0.00e+00      0.000
                                           APEX MAIN :        1   5.38e+00   5.38e+00    100.000
                                     background_work :        1   2.06e-05   2.06e-05      0.000
                       call_startup_functions_action :        1   0.00e+00   0.00e+00      0.000
                              load_components_action :        1   0.00e+00   0.00e+00      0.000
                                            pre_main :        1   0.00e+00   0.00e+00      0.000
                                          run_helper :        1   0.00e+00   0.00e+00      0.000
             

# Parallel Algorithms
HPX allows you to write loop parallel algorithms in a generic fashion, applying to specify the way in which parallelism is achieved (i.e. threads, distributed, cuda, etc.) through polcies.

In [ ]:
#include <hpx/include/parallel_for_each.hpp>
#include <hpx/parallel/algorithms/transform.hpp>
#include <boost/iterator/counting_iterator.hpp>

In [ ]:
vector<int> v = { 1, 2, 3, 4, 5, 6 };

## Transform
Here we demonstrate the transformation of a vector, and the various mechnanisms by which it can performed in parallel.

In [ ]:
.expr
// This parallel tranformation of vector v
// is done using thread parallelism. An
// implicit barrier is present at the end.
parallel::transform (
  parallel::par,
  begin(v), end(v), begin(v),
  [](int i) -> int
  {
    return i+1;  
  });
for(int i : v) cout << i << ",";

In [ ]:
.expr
// This parallel tranformation of vector v
// is done using thread parallelism. There
// is no implicit barrier. Instead, the
// transform returns a future.
auto  f = parallel::transform (
  parallel::par (parallel::v3::task),
  begin(v), end(v), begin(v),
  [](int i) -> int
  {
    return i+1;  
  });
  
// wait for the future to be ready.
f.wait();

for(int i : v) cout << i << ",";

In [ ]:
#include <hpx/include/parallel_fill.hpp>
#include <hpx/include/compute.hpp>
#include <hpx/include/parallel_executors.hpp>

In [ ]:
auto host_targets = hpx::compute::host::get_local_targets();
typedef hpx::compute::host::block_executor<> executor_type;
executor_type exec(host_targets);

In [ ]:
.expr
// Print out a list of the localities, i.e. hosts
// that can potentially be involved in this calculation.
// This notebook will probably show 1, alas.
for(auto host : host_targets)
  cout << host.get_locality() << endl;

In [ ]:
.expr
// This parallel tranformation of vector v
// is done using using distributed parallelism.
parallel::transform (
  parallel::execution::par.on(exec),
  begin(v), end(v), begin(v),
  [](int i) -> int
  {
    return i+1;  
  });

for(int i : v) cout << i << ",";

## Other Algorithms
There are a great many algorithms. Here we demonstrate "fill".

In [ ]:
.expr
std::vector<float> vd;
for(int i=0;i<10;i++) vd.push_back(1.f);
parallel::fill(parallel::execution::par.on(exec),vd.begin(),vd.end(),0.0f);

# Let’s Parallelize It – Adding Real Asynchrony

Here we take a step back. Instead of using a pre-designed parallel operation on a vector, we instead introduce task-level parallelism to an existing program.

Calculate Fibonacci numbers in parallel (1st attempt)

In [ ]:
uint64_t fibonacci(uint64_t n)
{
  // if we know the answer, we return the value
  if (n < 2) return n;
  // asynchronously calculate one of the sub-terms
  future<uint64_t> f = async(launch::async, &fibonacci, n-2);
  // synchronously calculate the other sub-term
  uint64_t r = fibonacci(n-1);
  // wait for the future and calculate the result
  return f.get() + r;
}

In [ ]:
.expr cout << fibonacci(10) << endl;

# Let’s Parallelize It – Introducing Control of Grain Size
Parallel calculation, switching to serial execution below given threshold

In [ ]:
const int threshold = 20;

uint64_t fibonacci_serial(uint64_t n)
{
  if (n < 2) return n;
  uint64_t f1 = fibonacci_serial(n-2);
  uint64_t f2 = fibonacci_serial(n-1);
  return f1 + f2;
}

uint64_t fibonacci2(uint64_t n)
{
  if (n < 2) return n;
  if (n < threshold) return fibonacci_serial(n);
  // asynchronously calculate one of the sub-terms
  future<uint64_t> f = async(launch::async, &fibonacci, n-2);
  // synchronously calculate the other sub-term
  uint64_t r = fibonacci2(n-1);
  // wait for the future and calculate the result
  return f.get() + r;
}

In [ ]:
.expr cout << fibonacci2(22) << endl;

# Let’s Parallelize It – Apply Futurization
Parallel way, futurize algorithm to remove suspension points

In [ ]:
future<uint64_t> fibonacci3(uint64_t n)
{
  if(n < 2) return make_ready_future(n);
  if(n < threshold) return make_ready_future(fibonacci_serial(n));

  future<uint64_t> f = async(launch::async, &fibonacci3, n-2);
  future<uint64_t> r = fibonacci3(n-1);

  return dataflow(
    [](future<uint64_t> f1, future<uint64_t> f2) {
      return f1.get() + f2.get();
    },
    f, r);
}


In [ ]:
.expr cout << fibonacci3(22).get() << endl;

# Let’s Parallelize It – Unwrap Argument Futures

In [ ]:
#include <hpx/util/unwrapped.hpp>

using hpx::util::unwrapped;

future<uint64_t> fibonacci4(uint64_t n)
{
  if(n < 2) return make_ready_future(n);
  if(n < threshold) return make_ready_future(fibonacci_serial(n));

  future<uint64_t> f = async(launch::async, &fibonacci4, n-2);
  future<uint64_t> r = fibonacci4(n-1);

  return dataflow(
    unwrapped([](uint64_t f1, uint64_t f2) {
      return f1+f2;
    }),
    f, r);
}


In [ ]:
.expr cout << fibonacci4(22).get() << endl;

### Excercise: Parallelize a sort

In [ ]:
#include <unistd.h>
#include <stdlib.h>
#include <iostream>
#include <vector>
#include <functional>
using namespace std;
function<void(vector<int>&)> myqsort = [](vector<int>& v)->void {};

In [ ]:
.expr
myqsort = [](vector<int>& v)->void {
  if(v.size()<2) return;
  vector<int> pre, eq, post;
  int pivot = v[rand() % v.size()];
  for(int val : v) {
    if(val < pivot) pre.push_back(val);
    else if(pivot < val) post.push_back(val);
    else eq.push_back(val);
  }
  myqsort(pre);
  myqsort(post);
  for(int i=0;i<pre.size();i++) v[i] = pre[i];
  for(int i=0;i<eq.size();i++) v[i+pre.size()] = eq[i];
  for(int i=0;i<post.size();i++) v[i+pre.size()+eq.size()] = post[i];
};
vector<int> vv{20};
for(int i=0;i<20;i++) vv.push_back(rand() % 100);
for(int val : vv) cout << val << " ";
cout << endl;
myqsort(vv);
for(int val : vv) cout << val << " ";
cout << endl;